In [8]:
import pandas as pd
import nltk
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem import SnowballStemmer
from nltk.stem import WordNetLemmatizer
from nltk.collocations import BigramCollocationFinder
import collections

## 1. Process train data

In [15]:
# adding to open , encoding='utf-8' is usually a good thing
with open('training_docs.txt','r', encoding='utf-8') as f:
    raw_train = f.read()
    
train_list = raw_train.split('EOD\n\n')
for i in range(len(train_list)):
    l = train_list[i].strip().split("\n")
    train_list[i] = l

# extract document id and text content
IDs = []
Texts = []
for l in train_list:
    if len(l) == 2:
        IDs.append(l[0][3:])
        Texts.append(l[1][5:])

# create data frame of train data
data = pd.DataFrame()
data['ID'] = IDs
data['Text'] = Texts

In [16]:
# extract labels of train data
with open('training_labels_final.txt','r') as f:
    label = f.read()
    
labels = label.split('\n')

for i in range(len(labels)):
    l = labels[i].split(' ')
    labels[i] = l
    
# there are 23 classes in total
label = []
for i in range(len(IDs)):
    if (labels[i][0] == IDs[i]):
        label.append(labels[i][1])

# combine into train dataframe
data['label'] = label
data.to_csv("train.csv", index=False)

In [17]:
data

ID                                               Text label
0            tr_doc_1  Two German tourists have been found safe and w...    C1
1            tr_doc_2  ACT police have seized a rare drug during a ra...    C1
2            tr_doc_3  A 50-year-old Brisbane man has been charged wi...    C1
3            tr_doc_4  In-depth discussions are continuing to resolve...    C1
4            tr_doc_5  Homicide detectives are still questioning a ma...    C1
5            tr_doc_6  The Cole Royal Commission has recommended crim...    C1
6            tr_doc_7  The dramatic hijacking of a Turkish airliner t...    C1
7            tr_doc_8  The hijacker of a Turkish plane has surrendere...    C1
8            tr_doc_9  The judge overseeing the trial in the United S...    C1
9           tr_doc_10  At least 68 people have been killed and 34 inj...    C1
10          tr_doc_11  Prosecutors in East Timor said they have indic...    C1
11          tr_doc_12  Drug dealers will be targeted today in a phone...    C1
12          tr_doc_13  A leading anti-war British Labour MP is denyin...    C1
13          tr_doc_14  A member of the Aboriginal Tent Embassy has th...    C1
14          tr_doc_15  Rockhampton teenager Natasha Ryan has broken d...    C1
15          tr_doc_16  Labor frontbencher Lindsay Tanner says the Gov...    C1
16          tr_doc_17  Bosnian Serb police and army are helping hide ...    C1
17          tr_doc_18  A US federal judge has found Iran Islamic Repu...    C1
18          tr_doc_19  A report by the Tasmanian Justice Department h...    C1
19          tr_doc_20  Two men have appeared in the Brisbane Magistra...    C1
20          tr_doc_21  Italy's financial police launched a major swoo...    C1
21          tr_doc_22  The Solomon Islands Foreign Minister is confid...    C1
22          tr_doc_23  A 19-year-old man has been treated in hospital...    C1
23          tr_doc_24  Federal Immigration Minister Philip Ruddock de...    C1
24          tr_doc_25  The two Telstra workers who were assaulted at ...    C1
25          tr_doc_26  The fourth suspect in an alleged Jemaah Islami...    C1
26          tr_doc_27  The Law Council of Australia says alleged Aust...    C1
27          tr_doc_28  A former US Marine who ran away to France with...    C1
28          tr_doc_29  A man has been murdered after a road rage chas...    C1
29          tr_doc_30  Police are continuing an investigation into th...    C1
...               ...                                                ...   ...
106415  tr_doc_106416  A senior Chinese Communist Party figure has sp...   C23
106416  tr_doc_106417  "We are living with dead hearts ... If we can'...   C23
106417  tr_doc_106418  The economic growth of China and shifting of U...   C23
106418  tr_doc_106419  Vietnamese border guards are refusing to stamp...   C23
106419  tr_doc_106420  China has granted its border patrol police the...   C23
106420  tr_doc_106421  Burma's opposition leader Aung San Suu Kyi has...   C23
106421  tr_doc_106422  South-East Asia's top diplomat has warned of g...   C23
106422  tr_doc_106423  A Chinese study published on World AIDS Day sa...   C23
106423  tr_doc_106424  The United States says it is deeply concerned ...   C23
106424  tr_doc_106425  Burma's President Thein Sein has asked the Opp...   C23
106425  tr_doc_106426  The Climate Institute CEO John Connor looks at...   C23
106426  tr_doc_106427  Chinese astronauts are preparing to grow fresh...   C23
106427  tr_doc_106428  A group of Nobel laureates have urged China's ...   C23
106428  tr_doc_106429  Independent space flight analyst Dr Morris Jon...   C23
106429  tr_doc_106430  An American intelligence report predicts China...   C23
106430  tr_doc_106431  A rights group says two more Tibetans have bur...   C23
106431  tr_doc_106432  Mo Yan has been lauded in Beijing for his Nobe...   C23
106432  tr_doc_106433  The United States has urged China and Japan to...   C23
106433  tr_doc_106434  The world's highest mountain should not be har

## 2. Process test data

In [18]:
# adding to open , encoding='utf-8' is usually a good thing
with open('testing_docs.txt','r', encoding='utf-8') as f:
    raw_test = f.read()
    
test_list = raw_test.split('EOD\n\n')
for i in range(len(test_list)):
    l = test_list[i].strip().split("\n")
    test_list[i] = l

# extract document id and text content
IDs = []
Texts = []
for l in test_list:
    if len(l) == 2:
        IDs.append(l[0][3:])
        Texts.append(l[1][5:])

# create data frame of train data
test = pd.DataFrame()
test['ID'] = IDs
test['Text'] = Texts

test.to_csv("test.csv", index=False)

## 3. Tokenizing, lemmatizing and stemming

In [11]:
# tokenize word
tokenizer = RegexpTokenizer(r"(?:\w+)+(?:[-'.](?:\w+)+)*")

# we should lower text first
tokenized = []
for text in Texts:
    tokenized.append(tokenizer.tokenize(text.lower()))

stopwords_list = set([stopword.encode('utf-8') for stopword in stopwords.words('english')])

filtered_list = []
for sent in tokenized:
    filtered_list.append([word.lower() for word in sent if str.encode(word.lower()) not in stopwords_list])

stemmer = SnowballStemmer('english')
stemmed = [[stemmer.stem(w) for w in para] for para in filtered_list]


[['two',
  'german',
  'tourists',
  'have',
  'been',
  'found',
  'safe',
  'and',
  'well',
  'after',
  'spending',
  'almost',
  'six',
  'hours',
  'lost',
  'in',
  'rugged',
  'rainforest',
  'at',
  'finch',
  'hatton',
  'gorge',
  'west',
  'of',
  'mackay',
  'last',
  'night',
  'it',
  'is',
  'the',
  'same',
  'area',
  'a',
  'young',
  'mackay',
  'man',
  'fell',
  'or',
  'jumped',
  'to',
  'his',
  'death',
  'last',
  'week',
  'sergeant',
  'jon',
  'purcell',
  'says',
  'rescuers',
  'located',
  'the',
  'missing',
  'pair',
  'just',
  'before',
  'midnight',
  'aest'],
 ['act',
  'police',
  'have',
  'seized',
  'a',
  'rare',
  'drug',
  'during',
  'a',
  'raid',
  'of',
  'a',
  'florey',
  'home',
  'police',
  'found',
  'a',
  'number',
  'of',
  'syringes',
  'filled',
  'with',
  'the',
  'drug',
  'ox-blood',
  'which',
  'is',
  'a',
  'form',
  'of',
  'amphetamine',
  'they',
  'also',
  'found',
  'a',
  'number',
  'of',
  'bags',
  'believed

In [25]:
lemmatizer = WordNetLemmatizer()
lemmatized = [[lemmatizer.lemmatize(w) for w in para] for para in stemmed]

wordlist = [word for para in lemmatized for word in set(para)]
word_counter = collections.Counter(wordlist)
most_freq = word_counter.most_common()[:20]

not_common = [word for word in word_counter if word_counter[word] == 1]

# remove the least and most frequence words
remove_words = set([word[0] for word in most_freq] + not_common)
remove_words

In [32]:
removed = []
for word in lemmatized:
    temp = []
    for x in word:
        if x not in remove_words:
            temp.append(x)
    removed.append(temp)
removed

[['german',
  'tourist',
  'found',
  'safe',
  'well',
  'spend',
  'almost',
  'six',
  'hour',
  'lost',
  'rug',
  'rainforest',
  'finch',
  'hatton',
  'gorg',
  'west',
  'mackay',
  'night',
  'area',
  'young',
  'mackay',
  'man',
  'fell',
  'jump',
  'death',
  'sergeant',
  'jon',
  'purcel',
  'rescuer',
  'locat',
  'miss',
  'pair',
  'midnight',
  'aest'],
 ['act',
  'polic',
  'seiz',
  'rare',
  'drug',
  'raid',
  'florey',
  'home',
  'polic',
  'found',
  'number',
  'syring',
  'fill',
  'drug',
  'form',
  'amphetamin',
  'found',
  'number',
  'bag',
  'believ',
  'contain',
  'crystal',
  'methamphetamin',
  '29-year-old',
  'woman',
  'charg',
  'number',
  'offenc',
  'face',
  'court',
  'morn',
  'act',
  'sergeant',
  'matt',
  'varley',
  'third',
  'drug',
  'found',
  'territori',
  'actual',
  'amphetamin',
  'manufactur',
  'process',
  'wherebi',
  'normal',
  'powder',
  'crystal',
  'produc',
  'liquid',
  'methamphetamin',
  'contain',
  'red',
 

In [33]:
wordlist = [word for para in removed for word in para]
finder = BigramCollocationFinder.from_words(wordlist)
finder.apply_freq_filter(10)
bigram_measures = nltk.collocations.BigramAssocMeasures()
bigrams = finder.nbest(bigram_measures.pmi,200)
bigrams

[('vennegoor', 'hesselink'),
 ('dal', 'broi'),
 ('hizb', 'ut-tahrir'),
 ('osteiti', 'pubi'),
 ('polona', 'hercog'),
 ('red-ear', 'slider'),
 ('machu', 'picchu'),
 ('steed', 'malbranqu'),
 ('boko', 'haram'),
 ('silvija', 'talaja'),
 ('ukuma', "ta'ai"),
 ('week-in', 'week-out'),
 ('golgol', 'mebrahtu'),
 ('bnp', 'pariba'),
 ('manas', 'manuokafoa'),
 ('marsel', 'ilhan'),
 ('rhett', 'lockyear'),
 ('timea', 'bacsinszki'),
 ('luk', 'chai'),
 ('eidur', 'gudjohnsen'),
 ('qiangba', 'puncog'),
 ('burkina', 'faso'),
 ('elio', "d'amato"),
 ('rudra', 'pratap'),
 ('isaka', 'cernak'),
 ('nue', 'dae'),
 ('atal', 'behari'),
 ('bilbo', 'baggin'),
 ('danai', 'udomchok'),
 ('servet', 'uzunlar'),
 ('edinson', 'cavani'),
 ('bran', 'nue'),
 ('wairangi', 'koopu'),
 ('tenz', 'norgay'),
 ('taulima', 'tautai'),
 ('klaas-jan', 'huntelaar'),
 ('daja', 'bedanova'),
 ('iva', 'majoli'),
 ('kohlberg', 'kravi'),
 ('sharm', 'el-sheikh'),
 ('vassallo', 'arguello'),
 ('mirko', 'vucin'),
 ('romina', 'oprandi'),
 ('piyush',

In [35]:
for para in removed:
    for j in range(0,len(para)-1):
        temp_tuple = (para[j], para[j+1])
        if temp_tuple in bigrams:
            para[j] = para[j] + '_' + para[j+1]
            para[j+1] = None

 ...]

In [42]:
final = []
for para in removed:
    para = [x for x in para if x != None]
    final.append(para)
final

[['german',
  'tourist',
  'found',
  'safe',
  'well',
  'spend',
  'almost',
  'six',
  'hour',
  'lost',
  'rug',
  'rainforest',
  'finch',
  'hatton',
  'gorg',
  'west',
  'mackay',
  'night',
  'area',
  'young',
  'mackay',
  'man',
  'fell',
  'jump',
  'death',
  'sergeant',
  'jon',
  'purcel',
  'rescuer',
  'locat',
  'miss',
  'pair',
  'midnight',
  'aest'],
 ['act',
  'polic',
  'seiz',
  'rare',
  'drug',
  'raid',
  'florey',
  'home',
  'polic',
  'found',
  'number',
  'syring',
  'fill',
  'drug',
  'form',
  'amphetamin',
  'found',
  'number',
  'bag',
  'believ',
  'contain',
  'crystal',
  'methamphetamin',
  '29-year-old',
  'woman',
  'charg',
  'number',
  'offenc',
  'face',
  'court',
  'morn',
  'act',
  'sergeant',
  'matt',
  'varley',
  'third',
  'drug',
  'found',
  'territori',
  'actual',
  'amphetamin',
  'manufactur',
  'process',
  'wherebi',
  'normal',
  'powder',
  'crystal',
  'produc',
  'liquid',
  'methamphetamin',
  'contain',
  'red',
 

In [44]:
data['text'] = final
data.head()

ID                                               Text label  \
0  tr_doc_1  Two German tourists have been found safe and w...    C1   
1  tr_doc_2  ACT police have seized a rare drug during a ra...    C1   
2  tr_doc_3  A 50-year-old Brisbane man has been charged wi...    C1   
3  tr_doc_4  In-depth discussions are continuing to resolve...    C1   
4  tr_doc_5  Homicide detectives are still questioning a ma...    C1   

                                                text  
0  [german, tourist, found, safe, well, spend, al...  
1  [act, polic, seiz, rare, drug, raid, florey, h...  
2  [50-year-old, brisban, man, charg, fraud, alle...  
3  [in-depth, discus, continu, resolv, safeti, co...  
4  [homicid, detect, still, question, man, fatal,...